#Biblhertz foto retrieval
This script parses through a local document called combined.xml in order to get for every object it describes their online images. It then stores usefull information for these objects on a local database.

@author: V.Bernasconi
@date: 25.11.2020

In [ ]:
import xml.etree.ElementTree as ET
import requests 
from bs4 import Bea8540
import pandas as pd
from xml.etree.ElementTree import parse

In [ ]:
document = parse('fototecca/combined.xml') #parse through the document combined.xml that is here stored in a local folder called /fototecca TO BE CHANGED ACCORDINGLY

In [ ]:
#Creation of an empty dataframe in which all needed information will be sored
df = pd.DataFrame(columns=['objectId','objectId_source','source','creator','date_begin','date_end','city', 'country', 'type', 'medium', 'dimensions', 'title'])

## Test for image download
This is a test to see if it is possible to download an image from their website. The image is then stored in a local folder called /images_bb (to be changed accordingly). Better run this test before going through the combined.xml file.

In [ ]:
#Simple check to see if the download of a picture works
img_link ="http://fotothek.biblhertz.it/bh/2048px/bhpd40708r.jpg"
response = requests.get(img_link)
if response:
    name = "images_bb/biblhertz_0.png"
    file = open(name, "wb")
    file.write(response.content)
    file.close()

## The actual big loop to scrap images
Loops over all objects present in the combined.xml file and searches for specific tags to downloads their corresponding image (if exists) and usefull information. Stores everything in a dataframe.

In [ ]:
i = 0
available_img = 0

#First loop iterate over all the different objects present in the file combined.xml
for item in document.iterfind('obj'):
    print(i)
    if item.findtext('a8450'): #search for the image id in the foto tag a8450
        for img_stuff in item.iterfind('a8450'):
            if img_stuff.findtext('a8540'): #if the image id exists, scrap the image online
                img_id = img_stuff.findtext('a8540')
                img_link ="http://fotothek.biblhertz.it/bh/2048px/"+img_id+".jpg"
                response = requests.get(img_link)
                if response: #if the image request is positive, download the image in the local folder "images_bb"
                    print("img_id ---")
                    print(img_id)
                    name = "images_bb/biblhertz_"+str(i)+".png"
                    file = open(name, "wb")
                    file.write(response.content)
                    file.close()
                    available_img = 1 #image is available
                    break
    else: #if there is no image for the object, go to next object
        print('NEXT --------------------------')
        continue
    if not available_img: #if it was not possible to download an image, go to next object
        print('NEXT --------------------------')
        continue
    else:
        available_img = 0
    
    #get the id of the object in the BB database
    if item.findtext('a5000'):
        objectID_source = item.findtext('a5000')
        print("objectID_source ---")
        print(objectID_source)
    #get information on the creator of the object
    if item.findtext('aob30'):
        for creator_stuff  in item.iterfind('aob30'):
            if creator_stuff.findtext('a3100'):
                painter = creator_stuff.findtext('a3100')
                break
            else:
                painter = 'unknown'
    else:
        painter = 'unknown'
    #get information on the creation date of the object
    if item.findtext('a5060'):
        for date_stuff in item.iterfind('a5060'):
            if date_stuff.findtext('a5064'):
                date = date_stuff.findtext('a5064')
                if '-' in date:
                    print(date)
                    date_from, date_to = date.split('-', 1)
                    break
                elif '/' in date:
                    print(date)
                    date_from, date_to = date.split('/', 1)
                    break
                else:
                    print(date)
                    date_from = date
                    date_to = date
                    break
            else:
                date_from = 'unknown'
                date_to = 'unknown'
    else:
        date_from = 'unknown'
        date_to = 'unknown'
    #get information on the location of the object
    if item.findtext('aob26'):
        for location_stuff in item.iterfind('aob26'):
            if location_stuff.findtext('a2664'):
                city = location_stuff.findtext('a2664')
                break
            else:
                city = 'unknown'
    else:
        city = 'unknown'
    #get information on the type of art
    if item.findtext('a5230'):
        art_type = item.findtext('a5230')
    else:
        art_type = 'unknown'
    #get information on the medium used for the object
    if item.findtext('a5300'):
        medium = item.findtext('a5300')
    else:
        medium = 'unknown'
    #get information on the dimension of the object
    if item.findtext('a5360'):
        dimensions = item.findtext('a5360')
    else:
        dimensions = 'unknown'
    #get information on the title of the object ### CHANGE HERE IF YOU ARE LOOKING FOR A SPECIFIC TITLE
    if item.findtext('a5200'):
        title = item.findtext('a5200')
    else:
        title = 'unknown'
        
    #append a new row to the dataframe holding all information collected on the object
    new_row = {'objectId': 'biblhertz_'+str(i), 'objectId_source': objectID_source,'source':'Bibliotheca Hertziana Rom','creator': painter,'date_begin': date_from,'date_end': date_to,'city': city, 'country': 'unknown', 'type': art_type, 'medium': medium, 'dimensions': dimensions, 'title':title}
    df = df.append(new_row, ignore_index=True)
    
    i+=1

0
NEXT --------------------------
0
NEXT --------------------------
0
NEXT --------------------------
0
img_id ---
bh543981
objectID_source ---
08132038
1
img_id ---
bh074830
objectID_source ---
08158402
2
NEXT --------------------------
2
img_id ---
bhim00010184
objectID_source ---
08027365
1849/1859
3
img_id ---
bh_gern_073540_post
objectID_source ---
08052321
4
img_id ---
bh_gern_028403_post
objectID_source ---
08020909
5
NEXT --------------------------
5
NEXT --------------------------
5
NEXT --------------------------
5
NEXT --------------------------
5
NEXT --------------------------
5
NEXT --------------------------
5
img_id ---
bh078782
objectID_source ---
08159866
6
NEXT --------------------------
6
NEXT --------------------------
6
NEXT --------------------------
6
NEXT --------------------------
6
img_id ---
bh000976
objectID_source ---
08109213
7
NEXT --------------------------
7
NEXT --------------------------
7
img_id ---
bhim00010183
objectID_source ---
08027364
1883
8
N

NEXT --------------------------
54
NEXT --------------------------
54
NEXT --------------------------
54
img_id ---
bh328449
objectID_source ---
08178098
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
NEXT --------------------------
55
img_id ---
bhpd49787
objectID_source ---
08062173
30ante/14ante
56
img_id ---
bh011526
objectID_source ---
08047895
57
img_id ---
bh_gern_028358_post
objectID_source ---
08020901
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------
58
NEXT --------------------------

img_id ---
bh257503
objectID_source ---
08171632
102
NEXT --------------------------
102
NEXT --------------------------
102
NEXT --------------------------
102
NEXT --------------------------
102
NEXT --------------------------
102
NEXT --------------------------
102
img_id ---
bh285264
objectID_source ---
08175598
103
NEXT --------------------------
103
NEXT --------------------------
103
img_id ---
bh009123
objectID_source ---
08014176
104
NEXT --------------------------
104
img_id ---
bh328443
objectID_source ---
08178092
105
NEXT --------------------------
105
NEXT --------------------------
105
NEXT --------------------------
105
NEXT --------------------------
105
img_id ---
bh163937
objectID_source ---
08168257
106
img_id ---
bh257504
objectID_source ---
08171633
107
NEXT --------------------------
107
NEXT --------------------------
107
NEXT --------------------------
107
NEXT --------------------------
107
NEXT --------------------------
107
NEXT --------------------------
10

img_id ---
bhpd31630
objectID_source ---
08085190
1708
160
NEXT --------------------------
160
NEXT --------------------------
160
NEXT --------------------------
160
img_id ---
bh199843
objectID_source ---
08103375
1638/1656
161
img_id ---
bh163936
objectID_source ---
08168256
162
NEXT --------------------------
162
NEXT --------------------------
162
img_id ---
bh257510
objectID_source ---
08171639
163
img_id ---
bh257509
objectID_source ---
08171638
164
img_id ---
bh078774
objectID_source ---
08159858
165
NEXT --------------------------
165
img_id ---
bh279120
objectID_source ---
08174134
166
NEXT --------------------------
166
img_id ---
bhim00032821
objectID_source ---
08119068
2003
167
NEXT --------------------------
167
img_id ---
bh285257
objectID_source ---
08175591
168
NEXT --------------------------
168
img_id ---
bhim00010195
objectID_source ---
08027369
1873
169
NEXT --------------------------
169
NEXT --------------------------
169
img_id ---
bhpd31631
objectID_source ---

img_id ---
bh074838
objectID_source ---
08158410
220
img_id ---
bh151407
objectID_source ---
08165740
221
NEXT --------------------------
221
NEXT --------------------------
221
img_id ---
bhim00041865
objectID_source ---
08109229
222
NEXT --------------------------
222
NEXT --------------------------
222
NEXT --------------------------
222
img_id ---
bh187862
objectID_source ---
08008284
1820.07.09
223
img_id ---
bhim00010204
objectID_source ---
08027372
1887
224
NEXT --------------------------
224
img_id ---
bh_gern_148553_post
objectID_source ---
08078702
225
NEXT --------------------------
225
NEXT --------------------------
225
NEXT --------------------------
225
NEXT --------------------------
225
NEXT --------------------------
225
NEXT --------------------------
225
NEXT --------------------------
225
img_id ---
bh012197
objectID_source ---
08095879
226
NEXT --------------------------
226
img_id ---
bh188791
objectID_source ---
08053770
227
img_id ---
bhim00015368
objectID_sour

...

img_id ---
bh075125
objectID_source ---
08158679
16451
NEXT --------------------------
16451
NEXT --------------------------
16451
NEXT --------------------------
16451
NEXT --------------------------
16451
img_id ---
bh_gern_073292_post
objectID_source ---
08052578
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
NEXT --------------------------
16452
img_id ---
bhfd311g12
objectID_source ---
08016309
1587
16453
NEXT --------------------------
16453
NEXT --------------------------
16453
img_id ---
bhpd62899
objectID_source ---
08003124
16454
img_id ---
bh_gern_073285_post
objectID_source ---
08052571
16455
NEXT --------------------------
16455
img_id ---
bh075122
objectID_source ---
08158676
16456
NEXT --------------------------
16456
NEXT --------------------------


img_id ---
bh086019
objectID_source ---
08109481
16513
NEXT --------------------------
16513
img_id ---
bhim00027949
objectID_source ---
08088792
1601/1700
16514
NEXT --------------------------
16514
NEXT --------------------------
16514
NEXT --------------------------
16514
NEXT --------------------------
16514
img_id ---
bh024255
objectID_source ---
08017791
16515
NEXT --------------------------
16515
NEXT --------------------------
16515
NEXT --------------------------
16515
img_id ---
bh134599
objectID_source ---
08115355
1801/1900
16516
img_id ---
bhpd43757r
objectID_source ---
08046687
1582-1583
16517
img_id ---
bh075116
objectID_source ---
08158670
16518
img_id ---
bhim00014343
objectID_source ---
08007920
16519
img_id ---
bh258073
objectID_source ---
08171890
16520
img_id ---
bh534079
objectID_source ---
08077508
16521
img_id ---
bhfd303h51
objectID_source ---
08016301
1451/1500
16522
NEXT --------------------------
16522
NEXT --------------------------
16522
NEXT -------------

img_id ---
bh398891
objectID_source ---
08039356
16578
NEXT --------------------------
16578
NEXT --------------------------
16578
img_id ---
bh001148
objectID_source ---
08036859
16579
NEXT --------------------------
16579
NEXT --------------------------
16579
img_id ---
bh155641
objectID_source ---
08167048
16580
NEXT --------------------------
16580
img_id ---
bhim00014336
objectID_source ---
08007916
1662-1664
16581
img_id ---
bh132277
objectID_source ---
08046691
1584-1586
16582
NEXT --------------------------
16582
img_id ---
bh_gern_095475_post
objectID_source ---
08068285
16583
img_id ---
bh216362
objectID_source ---
08170422
16584
NEXT --------------------------
16584
img_id ---
bh282278
objectID_source ---
08174382
16585
NEXT --------------------------
16585
NEXT --------------------------
16585
NEXT --------------------------
16585
img_id ---
bhim00013536
objectID_source ---
08129991
16586
NEXT --------------------------
16586
NEXT --------------------------
16586
NEXT -----

img_id ---
bh155633
objectID_source ---
08167040
16636
img_id ---
bh_gern_067043_post
objectID_source ---
08074163
16637
img_id ---
bhim00034342
objectID_source ---
08029514
16638
NEXT --------------------------
16638
NEXT --------------------------
16638
img_id ---
bh_gern_073284_post
objectID_source ---
08052570
16639
NEXT --------------------------
16639
NEXT --------------------------
16639
img_id ---
bhex-2020-05-178
objectID_source ---
08183641
1551/1600
16640
NEXT --------------------------
16640
NEXT --------------------------
16640


KeyboardInterrupt: 

In [ ]:
df

objectId objectId_source                     source  \
0          biblhertz_0        08132038  Bibliotheca Hertziana Rom   
1          biblhertz_1        08158402  Bibliotheca Hertziana Rom   
2          biblhertz_2        08027365  Bibliotheca Hertziana Rom   
3          biblhertz_3        08052321  Bibliotheca Hertziana Rom   
4          biblhertz_4        08020909  Bibliotheca Hertziana Rom   
...                ...             ...                        ...   
16635  biblhertz_16635        08167040  Bibliotheca Hertziana Rom   
16636  biblhertz_16636        08074163  Bibliotheca Hertziana Rom   
16637  biblhertz_16637        08029514  Bibliotheca Hertziana Rom   
16638  biblhertz_16638        08052570  Bibliotheca Hertziana Rom   
16639  biblhertz_16639        08183641  Bibliotheca Hertziana Rom   

                          creator date_begin date_end        city  country  \
0            Villamena, Francesco    unknown  unknown     unknown  unknown   
1               Tempesta, Antonio    unknown  unknown     unknown  unknown   
2                         unknown       1849     1859         Rom  unknown   
3                         unknown    unknown  unknown     unknown  unknown   
4                         unknown    unknown  unknown     unknown  unknown   
...                           ...        ...      ...         ...      ...   
16635  Mercati, Giovanni Battista    unknown  unknown     unknown  unknown   
16636  Wocher, Tiberius Dominikus    unknown  unknown     unknown  unknown   
16637            Tenerani, Pietro    unknown  unknown     unknown  unknown   
16638           Leonardo da Vinci    unknown  unknown     unknown  unknown   
16639                     unknown       1551     1600  Montefalco  unknown   

             type           medium      dimensions  \
0      Druckstock          unknown  27,8 x 27,8 cm   
1           Druck          unknown         unknown   
2           Büste          unknown         unknown   
3       Zeichnung  Feder & laviert      58 x 76 mm   
4       Zeichnung  Feder & laviert      80 x 71 mm   
...           ...              ...             ...   
16635       Druck          unknown         unknown   
16636   Zeichnung          unknown    168 x 117 mm   
16637      Statue          unknown         unknown   
16638   Zeichnung            Feder     108 x 74 mm   
16639    Kruzifix       geschnitzt       190 x 140   

                                                   title  
0      "Paniere Farnese" mit dem trunkenen Silen (von...  
1                                               die Jagd  
2                       Büste des Gnaeus Pompeius Magnus  
3                                  Ein Eber tötet Adonis  
4                              Zwei antike Gewandfiguren  
...                                                  ...  
16635                                                ...  
16636                        Bärtiger Mann in Landschaft  
16637                            Allegorie der Fischerei  
16638                            Kopf eines alten Mannes  
16639                                           Kruzifix  

[16640 rows x 12 columns]

## Storing information in sql database

In [ ]:
import sqlite3

In [ ]:
#create a connector to sql database on local repository (if the db does not exist, it should be created automatically)
conn = sqlite3.connect('artworks_db.db')
c = conn.cursor()

In [ ]:
#store a new table in the sql database
df.to_sql('Objects', conn, if_exists='append', index = False)

In [ ]:
#store the dataframe in your local repository
df.to_pickle("biblhertz_df")